In [1]:
from non_dominated_sort import fast_non_dominated_sort as fnds
from non_dominated_sort import dominance_check_between_two_points as dc
from non_dominated_sort import insert as insert
from non_dominated_sort import non_dominated_sorting as nds
from fitness_calculation import calculate_error_rate as error
from one_bit_purifying_search import one_bit_purifying_search as obps

In [2]:
import pandas as pd
import io
from sklearn.model_selection import train_test_split
import random
from sklearn import preprocessing

import math
from operator import itemgetter

In [3]:
from pymoo.indicators.hv import HV
import statistics

In [4]:
pd.set_option("display.max_columns",100)

In [5]:
#colnames = ['A1', 'A2', 'A3', 'A4', 'A5', 'A6', 'A7', 'A8', 'A9', 'A10', 'A11', 'A12', 'A13', 'A14', 'A15']
df = pd.read_csv('creditcard.csv',sep=',', encoding='utf-8', index_col=False )
#df_test = pd.read_csv('test.csv', sep=',', encoding='utf-8', index_col=False)
df.head()

Time        V1        V2        V3        V4        V5        V6        V7  \
0   0.0 -1.359807 -0.072781  2.536347  1.378155 -0.338321  0.462388  0.239599   
1   0.0  1.191857  0.266151  0.166480  0.448154  0.060018 -0.082361 -0.078803   
2   1.0 -1.358354 -1.340163  1.773209  0.379780 -0.503198  1.800499  0.791461   
3   1.0 -0.966272 -0.185226  1.792993 -0.863291 -0.010309  1.247203  0.237609   
4   2.0 -1.158233  0.877737  1.548718  0.403034 -0.407193  0.095921  0.592941   

         V8        V9       V10       V11       V12       V13       V14  \
0  0.098698  0.363787  0.090794 -0.551600 -0.617801 -0.991390 -0.311169   
1  0.085102 -0.255425 -0.166974  1.612727  1.065235  0.489095 -0.143772   
2  0.247676 -1.514654  0.207643  0.624501  0.066084  0.717293 -0.165946   
3  0.377436 -1.387024 -0.054952 -0.226487  0.178228  0.507757 -0.287924   
4 -0.270533  0.817739  0.753074 -0.822843  0.538196  1.345852 -1.119670   

        V15       V16       V17       V18       V19       V20       V21  \
0  1.468177 -0.470401  0.207971  0.025791  0.403993  0.251412 -0.018307   
1  0.635558  0.463917 -0.114805 -0.183361 -0.145783 -0.069083 -0.225775   
2  2.345865 -2.890083  1.109969 -0.121359 -2.261857  0.524980  0.247998   
3 -0.631418 -1.059647 -0.684093  1.965775 -1.232622 -0.208038 -0.108300   
4  0.175121 -0.451449 -0.237033 -0.038195  0.803487  0.408542 -0.009431   

        V22       V23       V24       V25       V26       V27       V28  \
0  0.277838 -0.110474  0.066928  0.128539 -0.189115  0.133558 -0.021053   
1 -0.638672  0.101288 -0.339846  0.167170  0.125895 -0.008983  0.014724   
2  0.771679  0.909412 -0.689281 -0.327642 -0.139097 -0.055353 -0.059752   
3  0.005274 -0.190321 -1.175575  0.647376 -0.221929  0.062723  0.061458   
4  0.798278 -0.137458  0.141267 -0.206010  0.502292  0.219422  0.215153   

   Amount  Class  
0  149.62      0  
1    2.69      0  
2  378.66      0  
3  123.50      0  
4   69.99      0

In [6]:
df.shape

(284807, 31)

In [7]:
# df = df.drop('Unnamed: 0', axis=1)
# df_test = df_test.drop('Unnamed: 0', axis=1)
# df.head(2)

In [8]:
df.shape

(284807, 31)

In [9]:
df['target'] = df['Class']
df = df.drop(['Class'], axis=1)

In [10]:
# df_test['target'] = df_test['Creditability']
# df_test = df_test.drop(['Creditability'], axis=1)

In [11]:
print(df.shape)
#print(df_test.shape)

(284807, 31)


In [12]:
df['target'].value_counts()

target
0    284315
1       492
Name: count, dtype: int64

In [13]:
#df_test['target'].value_counts()

In [14]:
df.head(1)

Time        V1        V2        V3        V4        V5        V6        V7  \
0   0.0 -1.359807 -0.072781  2.536347  1.378155 -0.338321  0.462388  0.239599   

         V8        V9       V10     V11       V12      V13       V14  \
0  0.098698  0.363787  0.090794 -0.5516 -0.617801 -0.99139 -0.311169   

        V15       V16       V17       V18       V19       V20       V21  \
0  1.468177 -0.470401  0.207971  0.025791  0.403993  0.251412 -0.018307   

        V22       V23       V24       V25       V26       V27       V28  \
0  0.277838 -0.110474  0.066928  0.128539 -0.189115  0.133558 -0.021053   

   Amount  target  
0  149.62       0

# Creating dummy variables

In [15]:
# train_up = pd.get_dummies(df, columns = ['Account.Balance', 'Payment.Status.of.Previous.Credit', 'Purpose', 'Sex...Marital.Status', 'Guarantors', 'Most.valuable.available.asset', 'Concurrent.Credits', 'Type.of.apartment', 'Occupation', 'Foreign.Worker', 'Telephone'], drop_first= True)
# test_up = pd.get_dummies(df_test, columns = ['Account.Balance', 'Payment.Status.of.Previous.Credit', 'Purpose', 'Sex...Marital.Status', 'Guarantors', 'Most.valuable.available.asset', 'Concurrent.Credits', 'Type.of.apartment', 'Occupation', 'Foreign.Worker', 'Telephone'], drop_first= True)


In [16]:
# print(train_up.shape)
# print(test_up.shape)

In [17]:
# train_up_null_count = train_up.isna().sum()
# train_up_null_count = train_up_null_count[train_up_null_count>0]
# train_up_null_count

In [18]:
# train_up = train_up.dropna()

In [19]:
# train_up.shape

In [20]:
# train_up.head(1)

In [21]:
# test_up_null_count = test_up.isna().sum()
# test_up_null_count = test_up_null_count[test_up_null_count>0]
# test_up_null_count

In [22]:
# test_up = test_up.dropna()

In [23]:
# test_up.shape

In [24]:
# test_up.head(1)

# Creating training test split

In [25]:
X = df.drop('target', axis=1)
y = df['target']

In [26]:
X_train, X_test, y_train, y_test = train_test_split(X,y , random_state=42,  test_size=0.30,  shuffle=True) 

In [27]:
# X_train = train_up.drop('target', axis=1)
# y_train = df['target']

# X_test = test_up.drop('target', axis=1)
# y_test = df_test['target']

In [28]:
X_test.columns

Index(['Time', 'V1', 'V2', 'V3', 'V4', 'V5', 'V6', 'V7', 'V8', 'V9', 'V10',
       'V11', 'V12', 'V13', 'V14', 'V15', 'V16', 'V17', 'V18', 'V19', 'V20',
       'V21', 'V22', 'V23', 'V24', 'V25', 'V26', 'V27', 'V28', 'Amount'],
      dtype='object')

In [29]:
X_train.shape

(199364, 30)

In [30]:
X_test.shape

(85443, 30)

In [31]:
y_train.value_counts()

target
0    199008
1       356
Name: count, dtype: int64

In [32]:
y_test.value_counts()

target
0    85307
1      136
Name: count, dtype: int64

In [33]:
def select_population_for_next_gen(population_size, P_t_plus_1_vector_fitness): 
    print("population_size" + str(population_size))
    print("len of P_t_plus_1_vector_fitness" + str(len(P_t_plus_1_vector_fitness)))
    P_t_plus_1 =  list(map(itemgetter(0), P_t_plus_1_vector_fitness))
    P_t_plus_1_fitness = list(map(itemgetter (1,2), P_t_plus_1_vector_fitness))
    P_t_plus_1_fitness = [list (item) for item in P_t_plus_1_fitness]
    
    sorted_index, sorted_values = fnds(data = P_t_plus_1_fitness)
    print("sorted_index")
    print(sorted_index)
    index_to_go_for_next_gen  = []
    
    for i in range(len(sorted_index)-1):
        if (len(sorted_index[i]) <= population_size - len(index_to_go_for_next_gen)):
            print("first if")
            print(len(sorted_index[i]))
            print(population_size - len(index_to_go_for_next_gen))
            index_to_go_for_next_gen = index_to_go_for_next_gen + sorted_index[i] 
        elif(len(index_to_go_for_next_gen) < population_size):
            places_left = population_size - len(index_to_go_for_next_gen)
            print("places_left")
            print(places_left)
            index_to_go_for_next_gen = index_to_go_for_next_gen + sorted_index[i][0:places_left] 
        else:
            print("neithr if")
    print("vedved index_to_go_for_next_gen")
    print(index_to_go_for_next_gen)
    population_for_next_gen = [P_t_plus_1_vector_fitness[i] for i in index_to_go_for_next_gen] 
    print("loop population_for_next_gen")
    print(population_for_next_gen)
    return population_for_next_gen

In [34]:
def top_front(P_t_plus_1_vector_fitness): 
    print("P_t_plus_1_vector_fitness")
    print(P_t_plus_1_vector_fitness)
    P_t_plus_1 = list(map(itemgetter(0), P_t_plus_1_vector_fitness))
    P_t_plus_1_fitness = list(map(itemgetter(1,2), P_t_plus_1_vector_fitness))
    P_t_plus_1_fitness = [list(item) for item in P_t_plus_1_fitness]
    
    print("P_t_plus_1_fitness")
    print(P_t_plus_1_fitness)
    print("before fnds")
    sorted_index, sorted_values = fnds(data = P_t_plus_1_fitness)
    print("after fnds")
    sorted_first_front_by_error = sorted(sorted_values[0], key = lambda x: x[0], reverse=True) 
    index_of_minimum_error_element = sorted_index[0][sorted_values[0].index(sorted_first_front_by_error[0])] 
     
    top_front = [P_t_plus_1[i] for i in sorted_index[0]]
    optimal_sol =  P_t_plus_1[index_of_minimum_error_element]
       
    return top_front

In [35]:
def optimal_sol(P_t_plus_1_vector_fitness): 
    P_t_plus_1 = list(map(itemgetter(0), P_t_plus_1_vector_fitness))
    P_t_plus_1_fitness = list(map(itemgetter(1,2), P_t_plus_1_vector_fitness))
    P_t_plus_1_fitness = [list(item) for item in P_t_plus_1_fitness]
    
    sorted_index, sorted_values = fnds(data = P_t_plus_1_fitness)
    sorted_first_front_by_error = sorted(sorted_values[0], key = lambda x: x[0], reverse=True) 
    index_of_minimum_error_element = sorted_index[0][sorted_values[0].index(sorted_first_front_by_error[0])] 
    
    top_front = [P_t_plus_1[i] for i in sorted_index[0]]
    optimal_sol =  P_t_plus_1[index_of_minimum_error_element]
    optimal_sol_fitness =  P_t_plus_1_fitness[index_of_minimum_error_element]
    
    return optimal_sol, optimal_sol_fitness

In [36]:
def MOFS(gen_max, obps_freq, dataset_train, target_train, dataset_test, target_test, initial_population):
    P_0 = initial_population
    all_gen_population_and_fitness = []
    num_feature = 30
    
    HV_list = []
    ref_point = np.array([30,1])
    mean_hv_of_prev_10_gen_list=[]
    difference_of_current_hv_and_mean_last_10_gen_list = []
    converged = False
    
    for t in (range(gen_max)):
        print("Attention - Generation " +str(t+1) + " starts")
        P_t_plus_1 = []
        P_t_plus_1_vector_fitness = []
        P_t_plus_1_vector = []
        P_t_plus_1_fitness = []
        round_robin_flag = 0
        N = len(P_0)
        print("NNNNNNNNNNNNNNNNNNNNNN")
        print(N)
        
        for i in range(1,N+1):
            random.seed(t+30*i)
            r1, r2, r3 = random.sample(range(0,N), 3)
            print(r1, r2, r3)
            print(P_0[r1],P_0[r2],P_0[r3])
            X_r1, num_feature_r1, f1_score_r1 = error(dataset_train=X_train, target_train = y_train, dataset_test = X_test, target_test = y_test, X_rn = P_0[r1])
            X_r2, num_feature_r2, f1_score_r2 = error(dataset_train=X_train, target_train = y_train, dataset_test = X_test, target_test = y_test, X_rn = P_0[r2])
            X_r3, num_feature_r3, f1_score_r3 = error(dataset_train=X_train, target_train = y_train, dataset_test = X_test, target_test = y_test, X_rn = P_0[r3])
            
            Dict_vector_cardinality_accuracy = {(num_feature_r1, f1_score_r1):X_r1, (num_feature_r2, f1_score_r2):X_r2, (num_feature_r3, f1_score_r3):X_r3 }
            num_feature_and_accuracy_for_3_candidate_sol = [[num_feature_r1, f1_score_r1], [num_feature_r2, f1_score_r2], [num_feature_r3, f1_score_r3]]
            
            res, smallest_key = nds(num_feature_and_accuracy_for_3_candidate_sol)
            res_smallest_key = res[smallest_key]
            
            res_smallest_key = sorted(res_smallest_key, key=lambda x:x[1], reverse = False)
            round_robin_flag = round_robin_flag + 1
            
            if(res_smallest_key[0] + res_smallest_key[0] != 0):
                X_best_t = res_smallest_key[0]
            else:
                X_best_t = res_smallest_key[1]
            
            removed_ = Dict_vector_cardinality_accuracy[tuple(X_best_t)]
            
            Dict_vector_cardinality_accuracy_after_removing_best = Dict_vector_cardinality_accuracy.copy()
            Dict_vector_cardinality_accuracy_after_removing_best.pop(tuple(X_best_t))
            
            list_of_Dict_vector_cardinality_accuracy_after_removing_best = list(Dict_vector_cardinality_accuracy_after_removing_best.items())
            
            if(len(list_of_Dict_vector_cardinality_accuracy_after_removing_best) == 0):
                X_r1_new = Dict_vector_cardinality_accuracy[tuple(X_best_t)]
                X_r2_new = Dict_vector_cardinality_accuracy[tuple(X_best_t)]
            elif(len(list_of_Dict_vector_cardinality_accuracy_after_removing_best) == 1):
                X_r1_new = list_of_Dict_vector_cardinality_accuracy_after_removing_best[0][1]
                X_r2_new = list_of_Dict_vector_cardinality_accuracy_after_removing_best[0][1]
            else:
                X_r1_new = list_of_Dict_vector_cardinality_accuracy_after_removing_best[0][1]
                X_r2_new = list_of_Dict_vector_cardinality_accuracy_after_removing_best[1][1]
                
            base_vector = Dict_vector_cardinality_accuracy[tuple(X_best_t)]
            X_i = P_0[i-1]
            
            X_ri, num_feature_ri, f1_score_ri = error(dataset_train=X_train, target_train = y_train, dataset_test = X_test, target_test = y_test, X_rn = X_i)
            X_rbase, num_feature_rbase, f1_score_rbase = error(dataset_train=X_train, target_train = y_train, dataset_test = X_test, target_test = y_test, X_rn = base_vector)
            
            xi_dominates_base, base_dominates_xi, base_and_xi_are_nondominating = dc(point1=[num_feature_rbase, f1_score_rbase], point2 =[num_feature_ri, f1_score_ri])
            
            X_r1_for_xor = X_r1_new.copy()
            X_r2_for_xor = X_r2_new.copy()
            
            sigma = 0.01
            c_i = [0]*num_feature
            v_i = [0]*num_feature
            F=0.1
            random.seed(t+30*i)
            random_val = random.sample(range(0,100), 1)
            random_value = random_val[0]/100
            
            if(base_dominates_xi == True):
                c_i = [sigma]*num_feature
            else:
                for i in range(num_feature):
                    c_i[i] = min(1, (F*int((bool(X_r1_for_xor[i]) ^ bool(X_r2_for_xor[i])))+sigma))
            mu = math.exp(-math.sqrt(t)) #t is generation count
            
            #for i in range(num_feature):
            #    v_i[i] = mu * (math.floor((X_r1[i] + X_r2[i] + X_r3[i])/1.5)) + (1-mu) *((base_vector[i] * int(bool(X_r1_new[i]) ^ bool(X_r2_new[i]))) + (int(not(bool(base_vector[i]))) * int(bool(X_r1_new[i]) & bool(X_r2_new[i]))))
            #    if(v_i[i] < 0.5):
            #        v_i[i] = 0
            #    else:
            #        v_i[i] = 1
                    
            for i in range(num_feature):
                if c_i[i] < random_value:
                    v_i[i] = base_vector[i]
                else:
                    v_i[i] = 1-base_vector[i]
                
            if sum(v_i)>0:
                pass
            else:
                v_i = base_vector
                
            random.seed(t+30*i)

            u_0_1 = random.sample(range(0,100), 1)[0]
            u_0_1 = u_0_1/100

            random.seed(t+30*i)
            h=random.sample(range(0,N),1)[0]
            cr=0.5
            u_i = [0]*num_feature
                
            for i in range(num_feature):
                if(u_0_1 < cr or i==h):
                    u_i[i] = v_i[i]
                else:
                    u_i[i] = X_i[i]
                        
            X_ui, num_feature_ui, f1_score_ui = error(dataset_train=X_train, target_train = y_train, dataset_test = X_test, target_test = y_test, X_rn = u_i)
            xi_dominates_ui, ui_dominates_xi, ui_and_xi_are_nondominating = dc(point1=[num_feature_ui, f1_score_ui], point2 =[num_feature_ri, f1_score_ri])

            if(xi_dominates_ui == 1):
                print("xi_dominates_ui")
                P_t_plus_1_vector_fitness.append([X_ri, num_feature_ri, f1_score_ri])
            elif(ui_dominates_xi == 1):
                print("ui_dominates_xi")
                P_t_plus_1_vector_fitness.append([X_ui, num_feature_ui, f1_score_ui])
            else:
                print("xi ui nondominating")
                P_t_plus_1_vector_fitness.append([X_ri, num_feature_ri, f1_score_ri])
                P_t_plus_1_vector_fitness.append([X_ui, num_feature_ui, f1_score_ui])
        
        print("P_t_plus_1_vector_fitnessP_t_plus_1_vector_fitnessP_t_plus_1_vector_fitnessP_t_plus_1_vector_fitness")
        print(P_t_plus_1_vector_fitness)
        
        #Remove duplicates
        P_t_plus_1_vector_fitness_unique=[]
        for i in P_t_plus_1_vector_fitness:
            if i not in P_t_plus_1_vector_fitness_unique:
                P_t_plus_1_vector_fitness_unique.append(i)
                
        dup_count = len(P_t_plus_1_vector_fitness) - len(P_t_plus_1_vector_fitness_unique)
        #print(dup_count)
        
        print("P_t_plus_1_vector_fitness")
        print(P_t_plus_1_vector_fitness)
        print("P_t_plus_1_vector_fitness_unique")
        print(P_t_plus_1_vector_fitness_unique)
        
        P_t_plus_1_vector_fitness = P_t_plus_1_vector_fitness_unique.copy()
        
        if(gen_max/(obps_freq+1) == math.ceil(gen_max/(obps_freq+1))):
            top_front_ = top_front(P_t_plus_1_vector_fitness=P_t_plus_1_vector_fitness)
            print("top_front_")
            print(top_front_)
            optimal_sol_, optimal_sol_fitness_ = optimal_sol(P_t_plus_1_vector_fitness=P_t_plus_1_vector_fitness)
            obps_result = obps(X_train, X_test, y_train, y_test, S=top_front_, optimal_sol = optimal_sol_)
                        
            to_be_removed_sol = optimal_sol_.copy()
            to_be_removed_fit = optimal_sol_fitness_.copy()
                       
            to_be_removed_sol = [to_be_removed_sol, to_be_removed_fit[0], to_be_removed_fit[1]]
            
            P_t_plus_1_vector_fitness.remove(to_be_removed_sol)
            P_t_plus_1_vector_fitness.append(obps_result[0])
        print("vedP_t_plus_1_vector_fitness")
        print(P_t_plus_1_vector_fitness)
        print("len of P_t_plus_1_vector_fitness")
        print(len(P_t_plus_1_vector_fitness))
        print(N)
        if len(P_t_plus_1_vector_fitness) > N:
            population_for_next_gen_ = select_population_for_next_gen(population_size=N, P_t_plus_1_vector_fitness=P_t_plus_1_vector_fitness)
        else:
            population_for_next_gen_ = P_t_plus_1_vector_fitness
        
        print("population_for_next_gen_population_for_next_gen_")
        print(population_for_next_gen_)
        all_gen_population_and_fitness.append(population_for_next_gen_)
        
        P_0 = list(map(itemgetter(0), population_for_next_gen_))
        
        if (len(P_0) < 3):
            print(f"stopped due to pupulation having size less than 3, i.e., size of {len(P_0)}")
            break
        
        print("Checking for convergence starts")
        P_0_metric = list(map(itemgetter(1,2), population_for_next_gen_))
        ind = HV(ref_point=ref_point)
        #print("HV for gen" + str(i+1), ind(np.array(P_0_metric)))
        HV_list.append(ind(np.array(P_0_metric)))
        print("HV_list till now is ")
        print(HV_list)
        
        
        #for i in range(len(HV_list)):
        if len(HV_list) > 10:
            i = len(HV_list)-1
            print(f"HV list has {i+1} elements now")
            mean_hv_of_prev_10_gen = statistics.mean(HV_list[i-10:i])
            print(f"mean_hv_of_prev_10_gen {mean_hv_of_prev_10_gen}")
            difference_of_current_hv_and_mean_last_10_gen = HV_list[i] - mean_hv_of_prev_10_gen
            print(f"difference_of_current_hv_and_mean_last_10_gen {difference_of_current_hv_and_mean_last_10_gen}")

            mean_hv_of_prev_10_gen_list.append(mean_hv_of_prev_10_gen)
            difference_of_current_hv_and_mean_last_10_gen_list.append(difference_of_current_hv_and_mean_last_10_gen)

            print("mean_hv_of_prev_10_gen_list")
            print(mean_hv_of_prev_10_gen_list)
            print("difference_of_current_hv_and_mean_last_10_gen_list")
            print(difference_of_current_hv_and_mean_last_10_gen_list)
            
            if(len(difference_of_current_hv_and_mean_last_10_gen_list)>=10):
                j=len(difference_of_current_hv_and_mean_last_10_gen_list)
                if(sum(difference_of_current_hv_and_mean_last_10_gen_list[j-10:j])<=0):
                    print(f"at gen {i+1} sum(difference_of_current_hv_and_mean_last_10_gen_list[j-10:j]) is less than zero, i.e., {sum(difference_of_current_hv_and_mean_last_10_gen_list[j-10:j])}")
                    print("difference_of_current_hv_and_mean_last_10_gen_list[j-10:j]")
                    print(difference_of_current_hv_and_mean_last_10_gen_list[j-10:j])
                    converged = True
                    print("converged is true now")
                    break
                else:
                    print(f"at gen {i+1} sum(difference_of_current_hv_and_mean_last_10_gen_list[j-10:j]) is NOT less than zero, i.e., {sum(difference_of_current_hv_and_mean_last_10_gen_list[j-10:j])}")
                    print("difference_of_current_hv_and_mean_last_10_gen_list[j-10:j]")
                    print(difference_of_current_hv_and_mean_last_10_gen_list[j-10:j])
                    print(f"at gen {i+1} is is not converged")
                    continue
            print("Checking for convergence ends")
                    
        if (converged == True):
            break
        
    return P_t_plus_1_vector_fitness, all_gen_population_and_fitness

In [37]:
import numpy as np
import random
Feature_population = []
rng = np.random.default_rng(30) #number of features
for i in range(50): #number of candidate solution in initial population
    array_of_0_1 = rng.random(30) #number of features
    array_of_0_1[array_of_0_1>=0.5] = 1
    array_of_0_1[array_of_0_1<0.5] = 0
    array_of_0_1=array_of_0_1.astype(int)
    list_of_0_1 = list(array_of_0_1)
    
    Feature_population.append(list_of_0_1)

In [38]:
len(Feature_population)

50

In [39]:
print(Feature_population)

[[0, 0, 0, 1, 1, 1, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 0, 1, 0, 0, 1, 1, 0, 0], [0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 1, 0, 0, 1, 0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0], [1, 0, 1, 1, 1, 0, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 1, 0, 1, 0, 0, 0, 0, 1, 1, 1, 1, 0], [0, 0, 0, 1, 0, 0, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0], [1, 0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 1], [0, 1, 0, 0, 0, 1, 1, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 1, 1, 0, 1, 0, 1, 1], [1, 0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 1, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 0, 0, 1, 0, 1, 0], [0, 0, 1, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 1, 1, 1, 0, 1, 0, 1, 0, 0, 1], [0, 0, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 0, 1, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1, 1, 0, 0, 0, 0, 1], [1, 1, 1, 0, 0, 1, 1, 1, 1, 0, 1, 1, 1, 0, 1, 1, 1, 1, 1, 0, 1, 0, 0, 0, 1, 1, 0, 0, 1, 0], [0, 1, 1, 1, 1, 1, 0, 0, 1, 0, 0, 0, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 

In [40]:
last_gen_vector_fitness, all_generation_population_and_fitness = MOFS(gen_max=100, obps_freq=1, dataset_train=X_train, target_train = y_train, dataset_test = X_test, target_test = y_test, initial_population = Feature_population)

Attention - Generation 1 starts
NNNNNNNNNNNNNNNNNNNNNN
50
34 18 39
[0, 1, 1, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 1, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 0, 0, 1, 1, 1] [1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 1, 1] [1, 0, 1, 1, 1, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 0, 1, 1, 1, 0, 0, 1, 1, 1, 1, 1]
f1 score is-0.8685258964143425
accuracy is0.9996137776061234
error rate is0.00038622239387664514
roc suc score is0.9007001270152991
gini is0.8014002540305982
[[85301     6]
 [   27   109]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.95      0.80      0.87       136

    accuracy                           1.00     85443
   macro avg       0.97      0.90      0.93     85443
weighted avg       1.00      1.00      1.00     85443

f1 score is-0.8319999999999999
accuracy is0.9995084442259752
error rate is0.0004915557740248211
roc suc score is0.8822943293392239
gini is0.7645

f1 score is-0.8740157480314961
accuracy is0.9996254813150287
error rate is0.00037451868497129226
roc suc score is0.908047207008045
gini is0.81609441401609
[[85300     7]
 [   25   111]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.94      0.82      0.87       136

    accuracy                           1.00     85443
   macro avg       0.97      0.91      0.94     85443
weighted avg       1.00      1.00      1.00     85443

f1 score is-0.8976377952755905
accuracy is0.9996957035684608
error rate is0.00030429643153917496
roc suc score is0.9190942023239249
gini is0.8381884046478498
[[85303     4]
 [   22   114]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.97      0.84      0.90       136

    accuracy                           1.00     85443
   macro avg       0.98      0.92      0.95     85443
weighted avg       1.00   

f1 score is-0.8692307692307693
accuracy is0.999602073897218
error rate is0.000397926102781998
roc suc score is0.915376703449617
gini is0.8307534068992339
[[85296    11]
 [   23   113]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.91      0.83      0.87       136

    accuracy                           1.00     85443
   macro avg       0.96      0.92      0.93     85443
weighted avg       1.00      1.00      1.00     85443

f1 score is-0.8605577689243027
accuracy is0.9995903701883126
error rate is0.0004096298116873509
roc suc score is0.897017795243339
gini is0.794035590486678
[[85300     7]
 [   28   108]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.94      0.79      0.86       136

    accuracy                           1.00     85443
   macro avg       0.97      0.90      0.93     85443
weighted avg       1.00      1

f1 score is-0.7477477477477479
accuracy is0.9993445923013002
error rate is0.0006554076986997615
roc suc score is0.8051294752723556
gini is0.6102589505447111
[[85304     3]
 [   53    83]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.97      0.61      0.75       136

    accuracy                           1.00     85443
   macro avg       0.98      0.81      0.87     85443
weighted avg       1.00      1.00      1.00     85443

f1 score is-0.8740157480314961
accuracy is0.9996254813150287
error rate is0.00037451868497129226
roc suc score is0.908047207008045
gini is0.81609441401609
[[85300     7]
 [   25   111]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.94      0.82      0.87       136

    accuracy                           1.00     85443
   macro avg       0.97      0.91      0.94     85443
weighted avg       1.00    

f1 score is-0.852589641434263
accuracy is0.9995669627705019
error rate is0.0004330372294980567
roc suc score is0.8933354634713792
gini is0.7866709269427583
[[85299     8]
 [   29   107]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.93      0.79      0.85       136

    accuracy                           1.00     85443
   macro avg       0.97      0.89      0.93     85443
weighted avg       1.00      1.00      1.00     85443

f1 score is-0.8016528925619835
accuracy is0.9994382219725431
error rate is0.0005617780274569384
roc suc score is0.8565648964053015
gini is0.7131297928106031
[[85298     9]
 [   39    97]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.92      0.71      0.80       136

    accuracy                           1.00     85443
   macro avg       0.96      0.86      0.90     85443
weighted avg       1.00   

...

f1 score is-0.900398406374502
accuracy is0.9997074072773662
error rate is0.0002925927226338221
roc suc score is0.915429454103139
gini is0.8308589082062781
[[85305     2]
 [   23   113]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.98      0.83      0.90       136

    accuracy                           1.00     85443
   macro avg       0.99      0.92      0.95     85443
weighted avg       1.00      1.00      1.00     85443

f1 score is-0.891566265060241
accuracy is0.9996839998595555
error rate is0.00031600014044452784
roc suc score is0.9080765129266684
gini is0.8161530258533367
[[85305     2]
 [   25   111]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.98      0.82      0.89       136

    accuracy                           1.00     85443
   macro avg       0.99      0.91      0.95     85443
weighted avg       1.00    

f1 score is-0.7203389830508474
accuracy is0.9992275552122467
error rate is0.0007724447877532903
roc suc score is0.81241208224413
gini is0.62482416448826
[[85292    15]
 [   51    85]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.85      0.62      0.72       136

    accuracy                           1.00     85443
   macro avg       0.92      0.81      0.86     85443
weighted avg       1.00      1.00      1.00     85443

f1 score is-0.891566265060241
accuracy is0.9996839998595555
error rate is0.00031600014044452784
roc suc score is0.9080765129266684
gini is0.8161530258533367
[[85305     2]
 [   25   111]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.98      0.82      0.89       136

    accuracy                           1.00     85443
   macro avg       0.99      0.91      0.95     85443
weighted avg       1.00      

f1 score is-0.891566265060241
accuracy is0.9996839998595555
error rate is0.00031600014044452784
roc suc score is0.9080765129266684
gini is0.8161530258533367
[[85305     2]
 [   25   111]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.98      0.82      0.89       136

    accuracy                           1.00     85443
   macro avg       0.99      0.91      0.95     85443
weighted avg       1.00      1.00      1.00     85443

f1 score is-0.900398406374502
accuracy is0.9997074072773662
error rate is0.0002925927226338221
roc suc score is0.915429454103139
gini is0.8308589082062781
[[85305     2]
 [   23   113]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.98      0.83      0.90       136

    accuracy                           1.00     85443
   macro avg       0.99      0.92      0.95     85443
weighted avg       1.00    

f1 score is-0.859437751004016
accuracy is0.9995903701883126
error rate is0.0004096298116873509
roc suc score is0.8933471858388284
gini is0.7866943716776569
[[85301     6]
 [   29   107]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.95      0.79      0.86       136

    accuracy                           1.00     85443
   macro avg       0.97      0.89      0.93     85443
weighted avg       1.00      1.00      1.00     85443

f1 score is-0.8951612903225806
accuracy is0.9996957035684608
error rate is0.00030429643153917496
roc suc score is0.9080823741103929
gini is0.8161647482207859
[[85306     1]
 [   25   111]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.99      0.82      0.90       136

    accuracy                           1.00     85443
   macro avg       1.00      0.91      0.95     85443
weighted avg       1.00  

f1 score is-0.864
accuracy is0.999602073897218
error rate is0.000397926102781998
roc suc score is0.8970236564270637
gini is0.7940473128541274
[[85301     6]
 [   28   108]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.95      0.79      0.86       136

    accuracy                           1.00     85443
   macro avg       0.97      0.90      0.93     85443
weighted avg       1.00      1.00      1.00     85443

f1 score is-0.864
accuracy is0.999602073897218
error rate is0.000397926102781998
roc suc score is0.8970236564270637
gini is0.7940473128541274
[[85301     6]
 [   28   108]]
              precision    recall  f1-score   support

           0       1.00      1.00      1.00     85307
           1       0.95      0.79      0.86       136

    accuracy                           1.00     85443
   macro avg       0.97      0.90      0.93     85443
weighted avg       1.00      1.00      1.00     85443



In [41]:
print(all_generation_population_and_fitness)

[[[[0, 1, 1, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 1, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 0, 0, 1, 1, 1], 14, 0.00038622239387664514], [[0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 1, 0, 0, 1, 0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0], 10, 0.0004798520651194682], [[0, 1, 0, 1, 1, 1, 0, 0, 1, 0, 1, 0, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 0, 0, 0, 0, 1, 1, 1, 0], 14, 0.000397926102781998], [[1, 0, 1, 1, 1, 0, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 1, 0, 1, 0, 0, 0, 0, 1, 1, 1, 1, 0], 16, 0.00037451868497129226], [[0, 0, 0, 1, 0, 0, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0], 15, 0.0004213335205927038], [[1, 1, 1, 1, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 1, 0, 0, 0, 1, 1, 0, 0, 1, 1, 0, 1, 0, 1, 0, 1], 18, 0.00031600014044452784], [[1, 0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 1], 16, 0.0005617780274569384], [[0, 1, 0, 0, 0, 1, 1, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 1, 1, 0, 1, 0, 1, 1], 13, 0.0004096298116873509], [[1, 1, 1, 0, 0, 1, 1, 1, 1,